In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import pandas as pd

In [ ]:
payments = pd.read_excel('/content/drive/MyDrive/hackaton_dataset/payments.xlsx', index_col=0) #Query result

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:237: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [ ]:
keywords = pd.read_excel('/content/drive/MyDrive/hackaton_dataset/keywords.xlsx', index_col=0)

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:237: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")


In [ ]:
payments.head()

amount             finished_at  campaign_id  \
id                                                     
5770251      70 2024-01-01 03:46:12.162         6236   
5770257     300 2024-01-01 03:48:40.075         6236   
5770269    1000 2024-01-01 04:04:09.024         6236   
5770272     500 2024-01-01 04:05:55.147         6236   
5770273      10 2024-01-01 04:07:11.539         6236   

                                      user_id  by_link   method app_version  \
id                                                                            
5770251  c096bde2-7808-9804-e893-9edad0881456    False     card      5.55.1   
5770257  fb16e315-373f-23c7-ff37-ccab13482859    False  sberpay      5.52.0   
5770269  6aeb378b-d6a9-ae3c-0684-6c357ee98e36    False  sberpay      5.55.1   
5770272  10f3f3f8-8314-6525-acb2-e0f00a7f4b38    False     card      5.51.1   
5770273  419206bd-f238-5ede-6862-872013b3ac8d    False     card      5.55.1   

        device_type sent_from  by_push  
id                                      
5770251     android      feed    False  
5770257         ios      feed    False  
5770269         ios      feed    False  
5770272         ios      feed    False  
5770273         ios      feed    False

In [ ]:
keywords.head()

campaign_id     text
keyword_id                      
2                  6903  Ребенок
2                  6369  Ребенок
2                  6441  Ребенок
2                  6414  Ребенок
2                  6385  Ребенок

In [ ]:
temp_df = payments[['user_id', 'campaign_id']]

In [ ]:
user_campaigns = temp_df.groupby('user_id')['campaign_id'].apply(list).reset_index()


In [ ]:
user_campaigns.head()

user_id  \
0  000171b6-2dbe-1fbf-5ac1-e4a547682dda   
1  000249bc-89dc-9a23-3db8-cce2252d43a7   
2  00028919-08e9-f41f-05f4-40792b4ff2e7   
3  00038fa3-68af-8f39-28d8-8cc04e38fde7   
4  00052c84-1928-8ee4-1052-7214fe2524e4   

                                         campaign_id  
0  [7231, 7194, 7245, 7242, 6413, 7056, 7271, 706...  
1  [7044, 6609, 6807, 6958, 6676, 6870, 6829, 703...  
2                                             [7130]  
3   [6343, 6202, 6118, 7044, 6925, 6785, 6800, 6798]  
4  [6424, 6490, 6497, 6497, 6537, 6536, 6682, 668...

In [ ]:
# Пример данных
# Создание DataFrame из примера данных
campaign_keywords = keywords.copy()

# Преобразование индекса в обычный столбец
campaign_keywords.reset_index(inplace=True)


In [ ]:
campaign_keywords.head()

keyword_id  campaign_id     text
0           2         6903  Ребенок
1           2         6369  Ребенок
2           2         6441  Ребенок
3           2         6414  Ребенок
4           2         6385  Ребенок

In [ ]:
# Создание словаря для быстрого доступа к ключевым словам по campaign_id
campaign_keywords_dict = campaign_keywords.groupby('campaign_id')['keyword_id'].apply(list).to_dict()

In [ ]:
# Функция для преобразования списка campaign_id в список уникальных ключевых слов
def get_unique_keywords(campaign_ids):
    keywords = []
    for cid in campaign_ids:
        if cid in campaign_keywords_dict:
            keywords.extend(campaign_keywords_dict[cid])
    return list(set(keywords))

In [ ]:
# Применение функции к каждому user_id
user_campaigns['unique_keywords'] = user_campaigns['campaign_id'].apply(get_unique_keywords)

# Создание новой таблицы с user_id и unique_keywords
user_unique_keywords = user_campaigns[['user_id', 'unique_keywords']]


In [ ]:
# Вывод новой таблицы
user_unique_keywords

In [ ]:
# Сохранение DataFrame в файл Excel
user_unique_keywords.to_excel('/content/drive/MyDrive/hackaton_dataset/dataset.xlsx', index=False)

In [ ]:
data = user_unique_keywords.copy()

In [ ]:
import lightgbm as lgb
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, MultiLabelBinarizer
from sklearn.multioutput import MultiOutputClassifier
from sklearn.metrics import accuracy_score

/usr/local/lib/python3.10/dist-packages/dask/dataframe/__init__.py:42: FutureWarning: 
Dask dataframe query planning is disabled because dask-expr is not installed.

You can install it with `pip install dask[dataframe]` or `conda install dask`.
This will raise in a future version.

  warnings.warn(msg, FutureWarning)


In [ ]:
# Encode categorical features
le_user_id = LabelEncoder()
data['user_id'] = le_user_id.fit_transform(data['user_id'])

In [ ]:
data

In [ ]:
# Binarize product categories
mlb = MultiLabelBinarizer()
data = data.join(pd.DataFrame(mlb.fit_transform(data.pop('unique_keywords')), columns=mlb.classes_))

In [ ]:
# Define features (X) and target (y)
X = data['user_id']
y = data[mlb.classes_]

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [ ]:
X_train_np = X_train.to_numpy()
X_train_np_reshaped = X_train_np.reshape(-1, 1)

In [ ]:
model = MultiOutputClassifier(lgb.LGBMClassifier(num_leaves=40, learning_rate=0.03, n_estimators=200))

In [ ]:
model.fit(X_train_np_reshaped, y_train)

In [ ]:
X_test_np = X_test.to_numpy()
X_test_np_reshaped = X_test_np.reshape(-1, 1)

In [ ]:
y_pred = model.predict(X_test_np_reshaped)


In [ ]:
y_pred.shape

(15788, 22)

In [ ]:
y_test

2   3   4   5   6   7   8   9   10  11  ...  15  16  17  18  19  20  \
60959   0   0   0   1   1   0   0   0   0   0  ...   0   0   0   0   0   0   
33943   1   1   1   1   1   0   0   1   0   0  ...   0   1   1   0   0   0   
60996   1   1   1   1   1   0   0   1   0   0  ...   0   1   0   1   1   0   
45141   1   1   1   1   1   1   1   1   0   0  ...   1   1   0   0   0   0   
39852   1   1   1   0   0   0   0   0   0   0  ...   0   0   0   0   0   0   
...    ..  ..  ..  ..  ..  ..  ..  ..  ..  ..  ...  ..  ..  ..  ..  ..  ..   
24075   1   0   0   1   0   0   0   0   0   0  ...   0   0   0   0   0   0   
51145   1   1   1   1   1   1   0   1   0   0  ...   1   1   0   0   0   0   
6860    1   1   1   1   1   0   1   1   0   0  ...   0   1   0   0   1   0   
18775   1   1   1   1   0   1   1   1   0   0  ...   0   0   1   1   1   0   
58814   1   1   0   0   1   1   1   0   1   0  ...   1   1   0   0   1   0   

       21  23  24  26  
60959   0   0   0   0  
33943   1   1   0   0  
60996   0   0   0   0  
45141   1   1   1   0  
39852   0   0   0   0  
...    ..  ..  ..  ..  
24075   0   0   0   0  
51145   1   0   0   0  
6860    0   0   0   0  
18775   0   0   0   0  
58814   1   1   0   1  

[15788 rows x 22 columns]

In [ ]:
r = y_test.loc[60959]

r

2     0
3     0
4     0
5     1
6     1
7     0
8     0
9     0
10    0
11    0
12    0
14    0
15    0
16    0
17    0
18    0
19    0
20    0
21    0
23    0
24    0
26    0
Name: 60959, dtype: int64

In [ ]:
accuracy_score(y_test.loc[60959], y_pred[0])

0.8181818181818182

In [ ]:
y_pred_reshaped = y_pred.reshape(22, 15788)

In [ ]:
y_pred_reshaped[0]

array([1, 1, 1, ..., 0, 0, 0])

In [ ]:
# Calculate accuracy for each product category and then find the average
accuracies = [accuracy_score(y_test[col], y_pred_reshaped[i]) for i, col in enumerate(y_test.columns)]

In [ ]:
avg_accuracy = sum(accuracies) / len(accuracies)

print(f'Average Accuracy: {avg_accuracy:.4f}')

Average Accuracy: 0.6100


In [ ]:
new_users = pd.DataFrame({
    'user_id': [12856]
})


In [ ]:
new_users_pred = model.predict(new_users)


In [ ]:
new_users_pred

array([[1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]])

In [ ]:
# Print predicted product categories for new users
for i, user_pred in enumerate(new_users_pred):
    print(f'User {i+1}: {mlb.inverse_transform(user_pred.reshape(1, -1))[0]}')

User 1: (2, 3, 4, 5, 6)


In [ ]:
import joblib

# Save the model
joblib.dump(model, '/content/drive/MyDrive/hackaton_dataset/multioutput_classifier_model.pkl')

['/content/drive/MyDrive/hackaton_dataset/multioutput_classifier_model.pkl']

In [ ]:
# Load the model
loaded_model = joblib.load('/content/drive/MyDrive/hackaton_dataset/multioutput_classifier_model.pkl')

In [ ]:
new_users_pred = loaded_model.predict(new_users)

In [ ]:
new_users_pred

array([[1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]])

In [ ]:
# Save the MultiLabelBinarizer
joblib.dump(mlb, '/content/drive/MyDrive/hackaton_dataset/multilabel_binarizer.pkl')

['/content/drive/MyDrive/hackaton_dataset/multilabel_binarizer.pkl']

In [ ]:
# Load the MultiLabelBinarizer
loaded_mlb = joblib.load('/content/drive/MyDrive/hackaton_dataset/multilabel_binarizer.pkl')

In [ ]:
# Print predicted product categories for new users
for i, user_pred in enumerate(new_users_pred):
    print(f'User {i+1}: {loaded_mlb.inverse_transform(user_pred.reshape(1, -1))[0]}')

User 1: (2, 3, 4, 5, 6)


In [ ]:
dictionary = dict(zip(user_unique_keywords['user_id'], data['user_id']))

print(dictionary)

{'000171b6-2dbe-1fbf-5ac1-e4a547682dda': 0, '000249bc-89dc-9a23-3db8-cce2252d43a7': 1, '00028919-08e9-f41f-05f4-40792b4ff2e7': 2, '00038fa3-68af-8f39-28d8-8cc04e38fde7': 3, '00052c84-1928-8ee4-1052-7214fe2524e4': 4, '0005768d-e69c-4690-7b26-82e027bebd70': 5, '00076c71-03b5-fe57-febb-9d8c04af4784': 6, '00089b6c-9a13-fb8b-57b6-6cdc03443ed2': 7, '0008f47d-a7f6-7684-b758-7dced7ed0dd7': 8, '0008fca4-040e-e06c-c21c-c2bbde126662': 9, '00096f9f-bd51-f8ca-c9a9-28f07b0d8444': 10, '0009a0e3-f309-b1eb-e761-66ae8c64fa05': 11, '000b442c-a409-009b-c88a-333f0b4d043b': 12, '000bddc0-2688-3c67-75c9-85e9f2315adc': 13, '000ce701-8b81-7c4d-5406-3f2e1fe5400f': 14, '000d6492-eb36-e52f-4e40-d7f16c9d7801': 15, '000e7799-969b-1e56-fead-8dd08465c21c': 16, '000f2ae8-e0e6-6753-86c2-f5e674e2f202': 17, '000fd570-a683-9aca-006f-d0872c1a1cd5': 18, '001065f0-c2bd-3db1-3ff1-99f9d82548ec': 19, '001198eb-caa5-9417-ec75-e224819afc01': 20, '0011b87a-87c6-ece0-dca7-d65ce32c5362': 21, '0013869d-714c-8ca1-e092-ba1a17e8a16a': 2

In [ ]:
import json

dict_path = '/content/drive/MyDrive/hackaton_dataset/dictionary.json'

# Сохранение словаря в файл
with open(dict_path, 'w') as file:
    json.dump(dictionary, file)

In [ ]:
with open(dict_path, 'r') as file:
    loaded_dictionary = json.load(file)

print(loaded_dictionary)

{'000171b6-2dbe-1fbf-5ac1-e4a547682dda': 0, '000249bc-89dc-9a23-3db8-cce2252d43a7': 1, '00028919-08e9-f41f-05f4-40792b4ff2e7': 2, '00038fa3-68af-8f39-28d8-8cc04e38fde7': 3, '00052c84-1928-8ee4-1052-7214fe2524e4': 4, '0005768d-e69c-4690-7b26-82e027bebd70': 5, '00076c71-03b5-fe57-febb-9d8c04af4784': 6, '00089b6c-9a13-fb8b-57b6-6cdc03443ed2': 7, '0008f47d-a7f6-7684-b758-7dced7ed0dd7': 8, '0008fca4-040e-e06c-c21c-c2bbde126662': 9, '00096f9f-bd51-f8ca-c9a9-28f07b0d8444': 10, '0009a0e3-f309-b1eb-e761-66ae8c64fa05': 11, '000b442c-a409-009b-c88a-333f0b4d043b': 12, '000bddc0-2688-3c67-75c9-85e9f2315adc': 13, '000ce701-8b81-7c4d-5406-3f2e1fe5400f': 14, '000d6492-eb36-e52f-4e40-d7f16c9d7801': 15, '000e7799-969b-1e56-fead-8dd08465c21c': 16, '000f2ae8-e0e6-6753-86c2-f5e674e2f202': 17, '000fd570-a683-9aca-006f-d0872c1a1cd5': 18, '001065f0-c2bd-3db1-3ff1-99f9d82548ec': 19, '001198eb-caa5-9417-ec75-e224819afc01': 20, '0011b87a-87c6-ece0-dca7-d65ce32c5362': 21, '0013869d-714c-8ca1-e092-ba1a17e8a16a': 2